In [11]:
import pandas as pd
from tqdm import tqdm
from collections import defaultdict

# movie.csv와 user, item, cluster, tsne좌표로 이루어진 데이터프레임을 생성합니다.
# 파일 경로와 실제 데이터에 맞게 코드를 수정해야 합니다.
data_dir = "/data/ephemeral/level2-movierecommendation-recsys-06/data/train/"
cluster_3d = f"kmeans3d_10cluster"
movie_df = pd.read_csv(data_dir + f"movie_{cluster_3d}.csv")
user_movie_df = pd.read_csv(data_dir + f"user_movie_{cluster_3d}.csv")

In [12]:
# 각 유저의 상위 n개 클러스터를 추출합니다.
n_cluster = 10 # 10의 약수로 선택하기
user_top_clusters = pd.Series(
    user_movie_df.groupby(["user", "cluster"])
    .size()
    .groupby("user")
    .nlargest(5)
    .reset_index(level=1, drop=True)
    , name="count"
).to_frame()
user_top_clusters

count
user   cluster       
11     2          102
       0           92
       1           57
       7           44
       6           30
...               ...
138493 2           98
       7           47
       0           39
       6           33
       1           27

[156794 rows x 1 columns]

In [13]:
cluster = defaultdict(dict)
for i, ser in movie_df.iterrows():
    cluster[ser["cluster"]][ser["item"]] = 0
cluster

defaultdict(dict,
            {2: {1: 0,
              2: 0,
              6: 0,
              8: 0,
              10: 0,
              13: 0,
              20: 0,
              23: 0,
              29: 0,
              44: 0,
              48: 0,
              60: 0,
              70: 0,
              89: 0,
              95: 0,
              107: 0,
              126: 0,
              145: 0,
              150: 0,
              158: 0,
              160: 0,
              165: 0,
              169: 0,
              170: 0,
              181: 0,
              185: 0,
              227: 0,
              231: 0,
              239: 0,
              288: 0,
              303: 0,
              313: 0,
              314: 0,
              329: 0,
              353: 0,
              355: 0,
              362: 0,
              364: 0,
              368: 0,
              376: 0,
              380: 0,
              393: 0,
              410: 0,
              420: 0,
              421: 0,
        

In [16]:
sorted_cluster = defaultdict(dict)
for key, values in cluster.items():
    for clus, cnt in sorted(values.items(), key=lambda x: x[1], reverse=True):
        sorted_cluster[key][clus] = cnt
sorted_cluster

defaultdict(dict,
            {2: {4993: 797,
              7153: 765,
              5952: 745,
              4306: 628,
              6539: 620,
              6874: 583,
              1136: 573,
              1: 572,
              6377: 553,
              8961: 552,
              5418: 548,
              4886: 508,
              1036: 491,
              364: 454,
              49272: 445,
              1197: 444,
              150: 433,
              60069: 429,
              48394: 401,
              8665: 387,
              46578: 387,
              4027: 381,
              54286: 377,
              588: 373,
              6016: 369,
              648: 354,
              5618: 353,
              2115: 349,
              924: 344,
              8360: 337,
              592: 332,
              8368: 325,
              68954: 320,
              1073: 317,
              3114: 314,
              48774: 307,
              40815: 303,
              590: 301,
              4896: 294,
      

In [17]:
user = defaultdict(list)
for i, ser in user_movie_df.iterrows():
    user[ser["user"]].append(ser["item"])
    cluster[ser["cluster"]][ser["item"]] += 1
user

defaultdict(list,
            {11: [880,
              2232,
              2720,
              2642,
              8977,
              1917,
              2916,
              2858,
              2959,
              6979,
              5444,
              3994,
              1591,
              5152,
              256,
              36509,
              2105,
              6503,
              54771,
              3083,
              33166,
              41571,
              3752,
              356,
              33660,
              364,
              1321,
              5283,
              48304,
              2827,
              7481,
              44191,
              19,
              48738,
              173,
              7099,
              3826,
              3969,
              2028,
              784,
              589,
              5219,
              67295,
              27441,
              5816,
              51412,
              608,
              2793,
              245

In [18]:
dic = defaultdict(list)
for u, c in user_top_clusters.index:
    cnt = 0
    for key, _ in sorted_cluster[c].items():
        if cnt == 2:
            break
        if key not in user[u]:
            dic["user"].append(u)
            dic["item"].append(key)
            cnt += 1
dic

defaultdict(list,
            {'user': [11,
              11,
              11,
              11,
              11,
              11,
              11,
              11,
              11,
              11,
              14,
              14,
              14,
              14,
              14,
              14,
              14,
              14,
              14,
              14,
              18,
              18,
              18,
              18,
              18,
              18,
              18,
              18,
              18,
              18,
              25,
              25,
              25,
              25,
              25,
              25,
              25,
              25,
              25,
              25,
              31,
              31,
              31,
              31,
              31,
              31,
              31,
              31,
              31,
              31,
              35,
              35,
              35,
              35,
  

In [19]:
submission = pd.DataFrame.from_dict(data=dic, orient="columns")
submission = submission.astype(int)
submission

user   item
0           11   8961
1           11   5418
2           11     47
3           11   7438
4           11   1732
...        ...    ...
313583  138493     47
313584  138493   2762
313585  138493  33794
313586  138493   1270
313587  138493   5349

[313588 rows x 2 columns]

In [ ]:
submission.to_csv("../data/eval/submission_3d_top_count.csv", index=False)